In [1]:
import xarray as xr
import numpy as np
import datetime
import glob
import argparse
import os
from dask.diagnostics import ProgressBar
ProgressBar().register()
import matplotlib.pyplot as plt
import cartopy
import resource
import matplotlib as mpl
import hvplot.xarray
import netCDF4
mpl.rcParams.update({'font.size': 18})

g = 9.81
EARTH_RADIUS = 6371
kn_to_ms = 0.51444
nmiles_to_km = 1.852

def ll2rb(lon1: np.ndarray,
          lat1: np.ndarray,
          lon2: np.ndarray,
          lat2: np.ndarray):
    """
    Given two points on the surface of a sphere, given by longitude and
    latitude pairs, computes the linear distance along the surface of
    the sphere between the two points (i.e. the Great Circle distance).

    INPUT:
    lon1: "Point 1" longitude, in decimal degrees.
    lat1: "Point 1" latitude, in decimal degrees.
    lon2: "Point 2" longitude, in decimal degrees.
    lat2: "Point 2" latitude, in decimal degrees.

    OUTPUT:
    dis: Great Circle distance, in kilometers.
    bearing: bearing between two points (in degrees)
    """

    lat1 = np.deg2rad(lat1)
    lon1 = np.deg2rad(lon1)
    lat2 = np.deg2rad(lat2)
    lon2 = np.deg2rad(lon2)

    sin_lat1 = np.sin(lat1)
    cos_lat1 = np.cos(lat1)
    sin_lat2 = np.sin(lat2)
    cos_lat2 = np.cos(lat2)
    delta_lon = lon2 - lon1
    cos_delta_lon, sin_delta_lon = np.cos(delta_lon), np.sin(delta_lon)
    x = np.sqrt(
        (cos_lat2 * sin_delta_lon) ** 2 +
        (cos_lat1 * sin_lat2 - sin_lat1 * cos_lat2 * cos_delta_lon) ** 2)
    y = sin_lat1 * sin_lat2 + cos_lat1 * cos_lat2 * cos_delta_lon

    dis = EARTH_RADIUS * np.arctan2(x, y)

    # bearing
    x = np.sin(delta_lon) * np.cos(lat2)
    y = np.cos(lat1) * np.sin(lat2) - np.sin(lat1) * np.cos(lat2) * np.cos(delta_lon)
    bearing = np.arctan2(x, y) / np.pi * 180.

    return dis, bearing

def coriolis(lat):
    '''Latitude must be in degrees.'''
    Omega = 7.2921e-5 # Earth rotation vector
    f = 2 * Omega * np.sin(lat * np.pi / 180) # Coriolis parameter at lat° latitude and assuming it's constant
    return f


def get_rmax_ck22(Vmax, R17, fcor, intercept, coef1, coef2):
    M17 = R17 * 1000 * 17.5 + 0.5 * fcor * ((R17 * 1000) ** 2)
    M_ratio = intercept * np.exp(coef1 * (Vmax - 17.5) + coef2 * (Vmax - 17.5) * 0.5 * fcor * R17 * 1000)
    Mmax = M_ratio * M17
    Rmax = (Vmax / fcor) * (np.sqrt(1 + (2 * fcor * Mmax) / (Vmax ** 2)) - 1)
    return Rmax

def get_TC_track(TC_atcf_id, ds):
    ds_TC_groups = ds.groupby('atcf_id')
    if TC_atcf_id.encode('ascii') not in ds_TC_groups.groups.keys():
        return(None)
    ds_TC_full = ds_TC_groups[TC_atcf_id.encode('ascii')]
    dates_surig = ds_TC_full.time
    to_keep = xr.DataArray(np.mod(dates_surig - np.datetime64("2000-01-01T00:00:00"), np.timedelta64(3, 'h')).astype(int), dims='sid')==0
    ds_TC = ds_TC_full.isel(sid=to_keep)
    ds_TC = ds_TC.rename({'storm_dir': 'translation_direction',
                          'pres': 'pc',
                          'poci': 'pn'}).drop_vars('sid').rename({'sid': 'date'}).rename({'time': 'date'}).set_coords('date')
    ds_TC['vmax'] = ds_TC.wind * kn_to_ms
    ds_TC['translation_speed'] = ds_TC.storm_speed * kn_to_ms
    #ds_TC['Rmax'] = ds_TC.rmw * nmiles_to_km
    TC_R34 = (xr.concat((ds_TC['r34_ne'],
                               ds_TC['r34_se'],
                               ds_TC['r34_sw'],
                               ds_TC['r34_nw']), dim='quadrant')).max('quadrant') * nmiles_to_km
    ds_TC['R34'] = TC_R34.where(np.logical_not(np.isnan(TC_R34)), 0)
    ds_TC['R50'] = (xr.concat((ds_TC['r50_ne'],
                               ds_TC['r50_se'],
                               ds_TC['r50_sw'],
                               ds_TC['r50_nw']), dim='quadrant')).max('quadrant') * nmiles_to_km
    ds_TC['R64'] = (xr.concat((ds_TC['r64_ne'],
                               ds_TC['r64_se'],
                               ds_TC['r64_sw'],
                               ds_TC['r64_nw']), dim='quadrant')).max('quadrant') * nmiles_to_km
    ds_TC['Rmax'] = get_rmax_ck22(ds_TC.vmax, ds_TC.R34, coriolis(ds_TC.lat), intercept=0.618, coef1=-0.00594, coef2=-0.00134) / 1000
    ds_TC['days_since_start'] = (ds_TC.date - ds_TC.date.isel(date=0)) / np.timedelta64(24*3600*1000000000,'ns')

    # Clean TC dataset
    ds_TC['Rmax_ibtracs'] = ds_TC.rmw * nmiles_to_km
    ds_TC['eye_diameter'] = ds_TC.eye * nmiles_to_km
    ds_TC['dist_to_land'] = ds_TC.dist2land * nmiles_to_km
    ds_TC = ds_TC.drop_vars(('record', 'wind', 'roci', 'gust', 'seahgt', 'searad_ne', 'searad_se', 'searad_nw', 'searad_sw', 'track_type', 'main_track_sid', 'landfall', 'storm_speed', 'ci', 'dp', 'tnum', 'gust_per', 'r50_dir', 'r50_long', 'r50_short', 'r30_dir', 'r30_long', 'r30_short', 'eye', 'dist2land', 'rmw'))
    name_printer = np.vectorize(lambda x: ''.join(np.bytes_(x).decode('ascii')))
    atcf_str = name_printer(ds_TC.atcf_id.isel(date=0).values)
    name_str = name_printer(ds_TC.name.isel(date=0).values)
    ds_TC = ds_TC.drop_vars(['atcf_id', 'name'])
    ds_TC.attrs['name'] = name_str
    ds_TC.attrs['atcf_id'] = atcf_str
    return(ds_TC)


def preprocess_alti(ds):
    if 'WIND_SPEED' not in list(ds.keys()):
        ds['WIND_SPEED'] = xr.full_like(ds.longitude, np.nan)
    return(ds)


def make_alti_product(TC_atcf_id):
    # Paths
    path_TCW = "/home1/datawork/cpouplin/TCW_V3_4/"
    path_alti = "/home/ref-cmems-public/tac/wave/WAVE_GLO_WAV_L3_SWH_NRT_OBSERVATIONS_014_001/"
    list_of_sats = ['j3', 'c2', 'cfo', 'al', 's3a', 's3b']
    netcdf_output_folder = "/home1/datawork/cpouplin/AltimeterProduct/"
    best_track_path_file = '/home/datawork-cersat-public/cache/users/jfpiolle/misc/ibtracs.nc'
    # Open Track
    #ds_Track = xr.open_dataset(glob.glob(f"{path_TCW}/S1WVL2/{TC_atcf_id}_*_S1WVL2_sat_S1A_l3_TCWAV.nc")[0], group='TC_track')

    output = "/home1/datawork/cpouplin/TCW_V3_4/"
    ds_ibtracs = xr.open_dataset(best_track_path_file)
    ds_Track = get_TC_track(TC_atcf_id, ds_ibtracs)

    list_of_ds_alti = []
    for sat in list_of_sats:
        print("sat", sat)
        list_of_files = []
        for dt in ds_Track.date.values[:-1]:
            dt_datetime = datetime.datetime.utcfromtimestamp(dt.astype('O') / 1e9)
            dt_datetime_after =  dt_datetime + datetime.timedelta(hours=3)
            dt_str = dt_datetime.strftime("%Y%m%dT%H%M%S")
            dt_str_after = dt_datetime_after.strftime("%Y%m%dT%H%M%S")
            potential_files = glob.glob(f"{path_alti}/dataset-wav-alti-l3-swh-rt-global-{sat}/{dt_datetime.year}/{str(dt_datetime.month).zfill(2)}/global_vavh_l3_rt_{sat}_{dt_str}_{dt_str_after}_*.nc")
            if len(potential_files) == 0:
                continue
            #print(sorted(potential_files)[-1]
            list_of_files.append(sorted(potential_files)[-1])
        if len(list_of_files) == 0:
            print(f"No sat {sat}")
            continue
        ds_alti = xr.open_mfdataset(list_of_files, combine='nested', concat_dim='time', coords='minimal', compat='override', parallel=True, preprocess=preprocess_alti).load()
        ds_alti = ds_alti.drop_duplicates('time')
        ds_alti['sat'] = xr.DataArray(np.array([sat] * ds_alti.sizes['time']), dims='time')
        list_of_ds_alti.append(ds_alti)
    if len(list_of_ds_alti) == 0:
        print("None sat")
        return(None)
    ds_alti_l3 = xr.concat(list_of_ds_alti, dim='time')

    # Interpolate track
    ds_Track_interp_lon = ds_Track.lon.interp(date=ds_alti_l3.time)
    ds_Track_interp_lat = ds_Track.lat.interp(date=ds_alti_l3.time)
    ds_Track_interp_R34 = ds_Track.R34.interp(date=ds_alti_l3.time)

    # Compute distance alti track
    dist_alti_track, azimuth_alti_track = ll2rb(ds_Track_interp_lon, ds_Track_interp_lat, ds_alti_l3.longitude, ds_alti_l3.latitude)
    ds_alti_l3['dist_alti_track'] = dist_alti_track
    ds_alti_l3['azimuth_alti_track'] = azimuth_alti_track

    # Co-locate alti track
    ds_alti_l3_TC = ds_alti_l3.where(dist_alti_track < 500 , drop=True).drop_vars('time').rename({'time': 'num_alti'})
    ds_alti_l3_TC['TC_atcf_id'] = xr.full_like(ds_alti_l3_TC.sat, TC_atcf_id)
    ds_alti_l3_TC['TC_name'] = xr.full_like(ds_alti_l3_TC.sat, ds_Track.name)
    if ds_alti_l3_TC.sizes['num_alti'] == 0:
        ds_alti_l3_TC = xr.Dataset()
    # Extract wave partitions data inside
    list_of_potential_S1A_files = glob.glob(f"{path_TCW}/S1WVL2/{TC_atcf_id}_*_S1WVL2_sat_S1A_l3_TCWAV.nc")
    list_of_potential_S1B_files = glob.glob(f"{path_TCW}/S1WVL2/{TC_atcf_id}_*_S1WVL2_sat_S1B_l3_TCWAV.nc")
    list_of_potential_CFO10_files = glob.glob(f"{path_TCW}/SWIML2S/{TC_atcf_id}_*_SWIML2S_incidence_10_l3_TCWAV.nc")
    list_of_potential_CFO08_files = glob.glob(f"{path_TCW}/SWIML2S/{TC_atcf_id}_*_SWIML2S_incidence_8_l3_TCWAV.nc")
    list_of_potential_CFO06_files = glob.glob(f"{path_TCW}/SWIML2S/{TC_atcf_id}_*_SWIML2S_incidence_6_l3_TCWAV.nc")
    list_of_potential_CFO04_files = glob.glob(f"{path_TCW}/SWIML2S/{TC_atcf_id}_*_SWIML2S_incidence_4_l3_TCWAV.nc")
    list_of_potential_CFO02_files = glob.glob(f"{path_TCW}/SWIML2S/{TC_atcf_id}_*_SWIML2S_incidence_2_l3_TCWAV.nc")

    list_of_inside_wave_ds = []
    if len(list_of_potential_S1A_files) == 1:
        ds_S1A = xr.open_dataset(list_of_potential_S1A_files[0], group='partition')[['date_obs', 'lon_obs', 'lat_obs', 'hs_obs', 'wl_obs', 'dir_obs', 'removed_ambiguity', 'wl_obs_ww3', 'dir_obs_ww3', 'hs_obs_ww3', 'spec_dist_obs_ww3', 'TC_step_wave_generation', 'dist_to_TC_center', 'flag_obs_in_R34']]
        ds_S1A['sat'] = xr.DataArray(np.array(['S1A'] * ds_S1A.sizes['num_part']), dims='num_part')
        if np.sum(ds_S1A.flag_obs_in_R34) > 0:
            ds_S1A_inside = ds_S1A.where(ds_S1A.flag_obs_in_R34, drop=True)
            list_of_inside_wave_ds.append(ds_S1A_inside)

    if len(list_of_potential_S1B_files) == 1:
        ds_S1B = xr.open_dataset(list_of_potential_S1B_files[0], group='partition')[['date_obs', 'lon_obs', 'lat_obs', 'hs_obs', 'wl_obs', 'dir_obs', 'removed_ambiguity', 'wl_obs_ww3', 'dir_obs_ww3', 'hs_obs_ww3', 'spec_dist_obs_ww3', 'TC_step_wave_generation', 'dist_to_TC_center', 'flag_obs_in_R34']]
        ds_S1B['sat'] = xr.DataArray(np.array(['S1B'] * ds_S1B.sizes['num_part']), dims='num_part')
        if np.sum(ds_S1B.flag_obs_in_R34) > 0:
            ds_S1B_inside = ds_S1B.where(ds_S1B.flag_obs_in_R34, drop=True)
            list_of_inside_wave_ds.append(ds_S1B_inside)

    if len(list_of_potential_CFO10_files) == 1:
        ds_CFO10 = xr.open_dataset(list_of_potential_CFO10_files[0], group='partition')[['date_obs', 'lon_obs', 'lat_obs', 'hs_obs', 'wl_obs', 'dir_obs', 'removed_ambiguity', 'wl_obs_ww3', 'dir_obs_ww3', 'hs_obs_ww3', 'spec_dist_obs_ww3', 'TC_step_wave_generation', 'dist_to_TC_center', 'flag_obs_in_R34']]
        ds_CFO10['sat'] = xr.DataArray(np.array(['CFO10'] * ds_CFO10.sizes['num_part']), dims='num_part')
        if np.sum(ds_CFO10.flag_obs_in_R34) > 0:
            ds_CFO10_inside = ds_CFO10.where(ds_CFO10.flag_obs_in_R34, drop=True)
            list_of_inside_wave_ds.append(ds_CFO10_inside)

    if len(list_of_potential_CFO08_files) == 1:
        ds_CFO08 = xr.open_dataset(list_of_potential_CFO08_files[0], group='partition')[['date_obs', 'lon_obs', 'lat_obs', 'hs_obs', 'wl_obs', 'dir_obs', 'removed_ambiguity', 'wl_obs_ww3', 'dir_obs_ww3', 'hs_obs_ww3', 'spec_dist_obs_ww3', 'TC_step_wave_generation', 'dist_to_TC_center', 'flag_obs_in_R34']]
        ds_CFO08['sat'] = xr.DataArray(np.array(['CFO08'] * ds_CFO08.sizes['num_part']), dims='num_part')
        if np.sum(ds_CFO08.flag_obs_in_R34) > 0:
            ds_CFO08_inside = ds_CFO08.where(ds_CFO08.flag_obs_in_R34, drop=True)
            list_of_inside_wave_ds.append(ds_CFO08_inside)

    if len(list_of_potential_CFO06_files) == 1:
        ds_CFO06 = xr.open_dataset(list_of_potential_CFO06_files[0], group='partition')[['date_obs', 'lon_obs', 'lat_obs', 'hs_obs', 'wl_obs', 'dir_obs', 'removed_ambiguity', 'wl_obs_ww3', 'dir_obs_ww3', 'hs_obs_ww3', 'spec_dist_obs_ww3', 'TC_step_wave_generation', 'dist_to_TC_center', 'flag_obs_in_R34']]
        ds_CFO06['sat'] = xr.DataArray(np.array(['CFO06'] * ds_CFO06.sizes['num_part']), dims='num_part')
        if np.sum(ds_CFO06.flag_obs_in_R34) > 0:
            ds_CFO06_inside = ds_CFO06.where(ds_CFO06.flag_obs_in_R34, drop=True)
            list_of_inside_wave_ds.append(ds_CFO06_inside)

    if len(list_of_potential_CFO04_files) == 1:
        ds_CFO04 = xr.open_dataset(list_of_potential_CFO04_files[0], group='partition')[['date_obs', 'lon_obs', 'lat_obs', 'hs_obs', 'wl_obs', 'dir_obs', 'removed_ambiguity', 'wl_obs_ww3', 'dir_obs_ww3', 'hs_obs_ww3', 'spec_dist_obs_ww3', 'TC_step_wave_generation', 'dist_to_TC_center', 'flag_obs_in_R34']]
        ds_CFO04['sat'] = xr.DataArray(np.array(['CFO04'] * ds_CFO04.sizes['num_part']), dims='num_part')
        if np.sum(ds_CFO04.flag_obs_in_R34) > 0:
            ds_CFO04_inside = ds_CFO04.where(ds_CFO04.flag_obs_in_R34, drop=True)
            list_of_inside_wave_ds.append(ds_CFO04_inside)

    if len(list_of_potential_CFO02_files) == 1:
        ds_CFO02 = xr.open_dataset(list_of_potential_CFO02_files[0], group='partition')[['date_obs', 'lon_obs', 'lat_obs', 'hs_obs', 'wl_obs', 'dir_obs', 'removed_ambiguity', 'wl_obs_ww3', 'dir_obs_ww3', 'hs_obs_ww3', 'spec_dist_obs_ww3', 'TC_step_wave_generation', 'dist_to_TC_center', 'flag_obs_in_R34']]
        ds_CFO02['sat'] = xr.DataArray(np.array(['CFO02'] * ds_CFO02.sizes['num_part']), dims='num_part')
        if np.sum(ds_CFO02.flag_obs_in_R34) > 0:
            ds_CFO02_inside = ds_CFO02.where(ds_CFO02.flag_obs_in_R34, drop=True)
            list_of_inside_wave_ds.append(ds_CFO02_inside)
    if len(list_of_inside_wave_ds) > 0:
        ds_wave_spec_inside = xr.concat(list_of_inside_wave_ds, dim='num_part')
        ds_wave_spec_inside['TC_atcf_id'] = xr.full_like(ds_wave_spec_inside.sat, TC_atcf_id)
        ds_wave_spec_inside['TC_name'] = xr.full_like(ds_wave_spec_inside.sat, ds_Track.name)

    else:
        ds_wave_spec_inside = xr.Dataset()
    # Make product
    filename = f"{ds_Track.attrs['atcf_id']}_{ds_Track.attrs['name']}_alti_l3_TCWAV.nc"
    print(filename)
    if not os.path.exists(netcdf_output_folder):
        os.makedirs(netcdf_output_folder)
    ds_Track = ds_Track.reset_index('date').reset_coords()
    tmpoutput = os.path.join(netcdf_output_folder, filename)
    ds_alti_l3_TC = ds_alti_l3_TC.load()
    ds_wave_spec_inside = ds_wave_spec_inside.load()
    ds_Track = ds_Track.load()
    ncfiles = netCDF4.Dataset(tmpoutput, mode='w')
    ncfiles.institution = "Laboratory of Physical and Spatial Oceanography, Institut Français pour la Recherche et l'Exploitation de la MER, European Space Agency"
    ncfiles.institution_abreviation = 'IFREMER-LOPS, ESA'
    ncfiles.product_version = "1.0"
    ncfiles.description = f"Description of the significant wave height inside tropical cyclone {ds_Track.attrs['atcf_id']}, {ds_Track.attrs['name']}, thanks to altimeters"

    ncfiles.close()
    display(ds_alti_l3_TC)
    ds_alti_l3_TC.to_netcdf(tmpoutput, group = '/altimeter', mode='a')
    ds_wave_spec_inside.to_netcdf(tmpoutput, group = '/spectral', mode='a')
    ds_Track.to_netcdf(tmpoutput, group = '/TC_track', mode='a')
    ds_alti_l3_TC.close()
    ds_wave_spec_inside.close()
    ds_Track.close()

In [2]:
make_alti_product("AL122021")

sat j3
[########################################] | 100% Completed |  0.9s
[########################################] | 100% Completed |  0.3s
sat c2
[########################################] | 100% Completed |  1.0s
[########################################] | 100% Completed |  0.3s
sat cfo
[########################################] | 100% Completed |  0.9s
[########################################] | 100% Completed |  0.3s
sat al
[########################################] | 100% Completed |  1.1s
[########################################] | 100% Completed |  0.3s
sat s3a
[########################################] | 100% Completed |  0.9s
[########################################] | 100% Completed |  0.3s
sat s3b
[########################################] | 100% Completed |  1.2s
[########################################] | 100% Completed |  0.3s
AL122021_LARRY_alti_l3_TCWAV.nc


<xarray.Dataset>
Dimensions:             (num_alti: 5000)
Coordinates:
    latitude            (num_alti) float64 19.79 19.74 19.69 ... 36.45 36.39
    longitude           (num_alti) float64 317.8 317.8 317.9 ... 302.8 302.7
    date                (num_alti) datetime64[ns] 2021-09-04T02:13:05.6262999...
Dimensions without coordinates: num_alti
Data variables:
    VAVH                (num_alti) float32 3.716 3.768 3.833 ... 6.63 6.542 6.39
    VAVH_UNFILTERED     (num_alti) float32 3.684 3.679 3.783 ... 6.595 6.407
    WIND_SPEED          (num_alti) float32 12.02 11.66 11.16 ... 14.35 13.89
    sat                 (num_alti) object 'j3' 'j3' 'j3' ... 's3b' 's3b' 's3b'
    dist_alti_track     (num_alti) float64 497.8 492.9 488.1 ... 492.4 496.8
    azimuth_alti_track  (num_alti) float64 12.26 12.64 13.04 ... 143.2 143.8
    TC_atcf_id          (num_alti) object 'AL122021' 'AL122021' ... 'AL122021'
    TC_name             (num_alti) object 'LARRY' 'LARRY' ... 'LARRY' 'LARRY'
Attributes: (12/28)
    Conventions:               CF-1.6
    first_meas_time:           2021-08-30 00:05:45.612683
    last_meas_time:            2021-08-30 02:59:59.996435
    comment:                   Significant Wave Height and Wind Speed measure...
    creator_email:             servicedesk.cmems@mercator-ocean.eu
    cdm_data_type:             swath
    ...                        ...
    equator_time:              2021-08-30T00:31:56.422000
    equator_longitude:         7.8
    creation_date:             2021-08-30T07:04:12
    product_version:           5_0
    software_version:          L3RT_SWH: (conf 2.4.3) (docker None); OCTANT: ...
    history:                   2021-08-30T07:04:12:Creation

/tmp/ipykernel_23647/1880217921.py:270: SerializationWarning: saving variable latitude with floating point data as an integer dtype without any _FillValue to use for NaNs
  ds_alti_l3_TC.to_netcdf(tmpoutput, group = '/altimeter', mode='a')
/tmp/ipykernel_23647/1880217921.py:270: SerializationWarning: saving variable longitude with floating point data as an integer dtype without any _FillValue to use for NaNs
  ds_alti_l3_TC.to_netcdf(tmpoutput, group = '/altimeter', mode='a')


In [3]:
ds_bill = xr.open_dataset('/home1/datawork/cpouplin/AltimeterProduct/AL122021_LARRY_alti_l3_TCWAV.nc', group='spectral')